In [ ]:
!pip install skforecast tqdm

In [3]:
import pandas as pd
from tqdm import tqdm
from sklearn.ensemble import HistGradientBoostingRegressor
import skforecast
from sklearn.feature_selection import RFECV
from skforecast.ForecasterAutoreg import ForecasterAutoreg
from skforecast.model_selection import bayesian_search_forecaster
from skforecast.model_selection import backtesting_forecaster
from skforecast.model_selection import select_features
import matplotlib.pyplot as plt
import numpy as np
import os
from os import path
import shutil
import re
import traceback
%matplotlib inline

In [4]:
# Regressor hyperparameters search space
def search_space(trial):

  # Lags grid
  lags_grid = tuple([12, 24, [1, 2, 3, 4, 7, 9, 24]])

  search_space  = {
      'max_iter'          : trial.suggest_int('max_iter', 400, 1200, step=100),
      'max_depth'         : trial.suggest_int('max_depth', 3, 10, step=1),
      'learning_rate'     : trial.suggest_float('learning_rate', 0.01, 1),
      'min_samples_leaf'  : trial.suggest_int('min_samples_leaf', 1, 20, step=1),
      'l2_regularization' : trial.suggest_float('l2_regularization', 0, 1),
      'lags'              : trial.suggest_categorical('lags', lags_grid)
  }
  return search_space


In [21]:
def search_hyperparameters(data, end_train, end_valid):
  # instantiate a forcaster transformer with categorical features
  forecaster = ForecasterAutoreg(
  regressor = HistGradientBoostingRegressor(
                  random_state=123),
  lags = 24
  )

  results_search, frozen_trial = bayesian_search_forecaster(
  forecaster         = forecaster,
  y                  = data.loc[:end_valid, 'temp'],
  search_space       = search_space,
  steps              = 36,
  refit              = False,
  metric             = 'mean_absolute_percentage_error',
  initial_train_size = len(data.loc[:end_train]),
  fixed_train_size   = False,
  n_trials           = 7,
  random_state       = 123,
  return_best        = True,
  n_jobs             = 'auto',
  verbose            = False,
  show_progress      = True
  )

  best_params = results_search['params'].iat[0]

  return best_params

In [22]:
# Define the function to return the SMAPE value
def smape(A, F):
    tmp = 2 * np.abs(F - A) / (np.abs(A) + np.abs(F))
    len_ = np.count_nonzero(~np.isnan(tmp))
    if len_ == 0 and np.nansum(tmp) == 0: # Deals with a special case
        return 100
    return round(100 / len_ * np.nansum(tmp), 3)

In [23]:
def recursive_train_predict(data, best_params, actual_data, end_valid, end_train, valid_num, train_num, df_idx, hzhnr01):

  # train for evaluation of the model
  forecaster = ForecasterAutoreg(
  regressor = HistGradientBoostingRegressor(**best_params,
                  random_state=123),
  lags = 24
  )
  print(hzhnr01)

  # train the model the time series train and validation dataset
  forecaster.fit(
    y    = data.loc[:end_train, 'temp'],
  )

  # # make predictions and evalute the model
  # predictions = forecaster.predict(
  #     steps    = 36
  # )
  # df_preds = pd.DataFrame(predictions)
  # preds = df_preds["pred"].values

  # evaluate on symmetric mean absolute percentage error
  #smape_value = smape(actual_data, preds)

  # train for future predictions
  forecaster = ForecasterAutoreg(
  regressor = HistGradientBoostingRegressor(**best_params,
                  random_state=123),
  lags = 24
  )
  # train the model the time series train and validation dataset
  forecaster.fit(
    y    = data.loc[:end_valid, 'temp']
  )

  # make predictions into the future
  predictions = forecaster.predict(
    steps    = 26
  )
  df_preds = pd.DataFrame(predictions)

  return df_preds

In [24]:
def recursive_populate_template(data_dir):
  preds_dict = {}

  # collect all files in the directory
  filenames = os.listdir(data_dir)
  filenames = filenames

  try:

    for filename in tqdm(filenames):

      hrbnz01 = filename.split(".")[0].split("-")[-1]
      filepath = path.join(data_dir, filename)
      df = pd.read_csv(filepath)[["date", "temp"]]
      df["date"] = pd.to_datetime(df["date"])
      df.set_index("date", inplace=True)
      df.index = pd.date_range(start=df.index.min(), end=df.index.max(), freq='MS')

      data = df.copy()
      df_idx = data.index
      train_num = int(len(data) * 0.8)
      valid_num = len(data.loc[:"2021-11-01"])
      end_train = df_idx[train_num]
      end_valid = df_idx[valid_num]
      end_evaluation = df_idx[train_num+36]
      evaluate_data = data.loc[df_idx[train_num+1]: end_evaluation, "temp"].values

      # tune for best hyperparamters and evaluate on MAPE metric
      best_params = search_hyperparameters(data, end_train, end_valid)

      # train and make predict into 26 months in the future of the test template
      df_predictions = recursive_train_predict(data,best_params, evaluate_data, end_valid, end_train, valid_num, train_num, df_idx, hrbnz01)
      df_predictions["pred"] =  df_predictions["pred"].round(2)
      preds_dict[hrbnz01] = df_predictions['pred'].values


  except Exception as ex:
    print("[Error]")
    print(traceback.format_exc())

  df_final_preds = pd.DataFrame(preds_dict, index=range(26))
  df_final_preds.index = pd.date_range(start=pd.Timestamp("2021-12-01") + pd.DateOffset(months=1), periods=26, freq='MS')
  print("> Done")

  return df_final_preds

In [25]:
processed_data_dir = "/content/drive/MyDrive/temp_processed_data"


df_submission = recursive_populate_template(processed_data_dir)
df_submission.to_csv("df_submission.csv")
# df_smape.to_csv("smape_score.csv", index=False)

  0%|          | 0/487 [00:00<?, ?it/s]

  0%|          | 0/7 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/optuna/distributions.py:524: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [1, 2, 3, 4, 7, 9, 24] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(


`Forecaster` refitted using the best-found lags and parameters, and the whole data set: 
  Lags: [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24] 
  Parameters: {'max_iter': 1000, 'max_depth': 5, 'learning_rate': 0.2345829390285611, 'min_samples_leaf': 12, 'l2_regularization': 0.7194689697855631}
  Backtesting metric: 0.016323670319101133

305524


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:278: UserWarning: Feature 0 is constant and will be replaced with 0.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(
  0%|          | 1/487 [00:15<2:05:23, 15.48s/it]

...

/usr/local/lib/python3.10/dist-packages/optuna/distributions.py:524: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [1, 2, 3, 4, 7, 9, 24] which is of type list.
  warnings.warn(message)
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(


`Forecaster` refitted using the best-found lags and parameters, and the whole data set: 
  Lags: [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24] 
  Parameters: {'max_iter': 700, 'max_depth': 6, 'learning_rate': 0.43157198739286967, 'min_samples_leaf': 7, 'l2_regularization': 0.4263513069628082}
  Backtesting metric: 0.028658980992476178

319699


/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(
100%|██████████| 487/487 [1:57:58<00:00, 14.53s/it]

> Done



<frozen importlib._bootstrap>:914: ImportWarning: _PyDrive2ImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:914: ImportWarning: _PyDriveImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:914: ImportWarning: _GenerativeAIImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:914: ImportWarning: _OpenCVImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:914: ImportWarning: APICoreClientInfoImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:914: ImportWarning: _BokehImportHook.find_spec() not found; falling back to find_module()
<frozen importlib._bootstrap>:914: ImportWarning: _AltairImportHook.find_spec() not found; falling back to find_module()


In [26]:
#df_submission.index = pd.date_range(start=pd.Timestamp("2021-12-01") + pd.DateOffset(months=1), periods=26, freq='MS')
df_submission

305524  345504  345470  335430  316000  306415  326074  326504  \
2022-01-01   12.33   12.78    9.60   12.28   12.44   11.31   12.43   11.14   
2022-02-01   11.69   12.25    8.11   11.70   12.40   11.35   12.40   10.84   
2022-03-01   11.44   12.09    7.64   11.30   12.41   11.48   12.43   10.93   
2022-04-01   11.14   11.90    8.76   10.98   12.38   11.33   12.37   11.02   
2022-05-01   11.10   11.57   10.12   10.87   12.36   11.53   12.38   11.03   
2022-06-01   11.20   11.47   10.21   10.87   12.53   11.64   12.54   11.01   
2022-07-01   11.29   11.56   12.51   11.30   12.48   11.60   12.50   10.93   
2022-08-01   11.50   11.82   14.21   11.70   12.45   11.61   12.48   10.99   
2022-09-01   11.83   12.07   15.14   12.29   12.48   11.44   12.52   11.05   
2022-10-01   12.20   12.51   15.44   12.47   12.48   11.45   12.45   10.98   
2022-11-01   12.40   12.90   13.68   13.02   12.50   11.49   12.51   10.90   
2022-12-01   12.40   13.29   11.36   12.95   12.46   11.27   12.48   10.78   
2023-01-01   12.01   12.72   10.07   12.38   12.35   11.29   12.38   10.80   
2023-02-01   11.43   12.48    8.15   11.71   12.31   11.58   12.44   10.88   
2023-03-01   11.08   12.13    8.02   11.43   12.26   11.33   12.44   10.93   
2023-04-01   10.84   12.07    8.43   11.07   12.33   11.48   12.48   10.96   
2023-05-01   10.80   12.02    9.59   11.07   12.30   11.53   12.44   11.02   
2023-06-01   10.90   11.84   10.83   11.09   12.28   11.50   12.37   11.01   
2023-07-01   11.05   11.66   12.46   11.11   12.39   11.64   12.49   11.23   
2023-08-01   11.30   11.89   14.26   11.13   12.44   11.65   12.45   11.64   
2023-09-01   11.59   12.23   15.35   11.54   12.49   11.62   12.46   12.24   
2023-10-01   12.03   12.52   15.34   12.23   12.59   11.67   12.53   12.46   
2023-11-01   12.20   12.97   14.13   12.19   12.59   11.45   12.39   12.43   
2023-12-01   12.35   13.19   12.01   12.31   12.50   11.26   12.40   11.90   
2024-01-01   12.33   13.18   10.31   12.43   12.48   11.41   12.49   11.23   
2024-02-01   11.69   12.81    8.03   12.29   12.51   11.30   12.46   10.83   

            345538  316174  ...  313064  319764  319772  312736  333088  \
2022-01-01   11.52   12.24  ...   11.35   13.64   12.50   11.88   12.63   
2022-02-01   11.52   11.54  ...   10.83   13.07   11.83    9.76   11.89   
2022-03-01   11.52   10.83  ...   11.13   12.18   11.28    8.69   11.58   
2022-04-01   11.52   10.60  ...   11.36   11.03   11.41    8.60   11.57   
2022-05-01   11.52   11.08  ...   11.97   10.99   11.75    9.24   11.78   
2022-06-01   11.52   11.61  ...   12.59   11.50   11.91   11.95   12.41   
2022-07-01   11.49   12.26  ...   13.35   12.27   12.50   15.54   12.63   
2022-08-01   11.51   13.66  ...   13.89   12.87   12.72   19.02   13.03   
2022-09-01   11.49   14.52  ...   14.51   13.54   13.24   19.44   13.33   
2022-10-01   11.50   14.84  ...   14.38   13.87   13.60   19.23   13.59   
2022-11-01   11.50   14.32  ...   13.49   13.94   13.71   17.77   13.82   
2022-12-01   11.51   12.82  ...   11.24   13.85   13.75   14.64   13.64   
2023-01-01   11.54   12.56  ...   10.29   13.60   12.67   12.23   12.36   
2023-02-01   11.55   11.53  ...   10.49   13.03   11.98    9.70   11.84   
2023-03-01   11.60   10.86  ...   10.42   12.96   11.52    8.54   11.49   
2023-04-01   11.58   10.54  ...   10.55   13.29   11.67    8.56   11.36   
2023-05-01   11.61   11.20  ...   10.77   13.55   11.94    9.23   11.99   
2023-06-01   11.53   11.89  ...   11.09   13.55   12.36   11.77   12.32   
2023-07-01   11.52   12.77  ...   11.78   13.61   12.57   15.19   12.66   
2023-08-01   11.48   13.70  ...   13.34   13.76   12.70   18.62   12.81   
2023-09-01   11.48   14.61  ...   13.92   13.85   13.24   19.47   13.26   
2023-10-01   11.43   14.97  ...   13.17   13.82   13.60   18.88   13.61   
2023-11-01   11.31   14.61  ...   12.11   13.89   13.84   17.57   13.63   
2023-12-01   11.29   13.11  ...   11.17   13.91   13.84   14.74   13.63   
2024-01-01   11.28   12.44  ..

In [9]:
df = pd.read_csv("/content/drive/MyDrive/Burgenland-300137.csv")[["date", "temp"]]
df["date"] = pd.to_datetime(df["date"])
df.set_index("date", inplace=True)
df.index = pd.date_range(start=df.index.min(), end=df.index.max(), freq='MS')

data = df.copy()
df_idx = data.index
train_num = int(len(data) * 0.8)
valid_num = len(data.loc[:"2021-11-01"])
end_train = df_idx[train_num]
end_valid = df_idx[valid_num]
end_evaluation = df_idx[train_num+30]
evaluate_data = data.loc[df_idx[train_num+1]: end_evaluation, "temp"].values
df

temp
1962-12-01  11.77
1963-01-01  11.77
1963-02-01  11.77
1963-03-01  11.77
1963-04-01  11.77
...           ...
2023-10-01    NaN
2023-11-01    NaN
2023-12-01    NaN
2024-01-01    NaN
2024-02-01    NaN

[735 rows x 1 columns]

In [12]:
# instantiate a forcaster transformer with categorical features
forecaster = ForecasterAutoreg(
regressor = HistGradientBoostingRegressor(
                random_state=123),
lags = 24
)

In [15]:
# Regressor hyperparameters search space
def search_space(trial):

  # Lags grid
  lags_grid = tuple([12, 24, [1, 2, 3, 4, 7, 9, 24]])

  search_space  = {
      'max_iter'          : trial.suggest_int('max_iter', 400, 1200, step=100),
      'max_depth'         : trial.suggest_int('max_depth', 3, 10, step=1),
      'learning_rate'     : trial.suggest_float('learning_rate', 0.01, 1),
      'min_samples_leaf'  : trial.suggest_int('min_samples_leaf', 1, 20, step=1),
      'l2_regularization' : trial.suggest_float('l2_regularization', 0, 1),
      'lags'              : trial.suggest_categorical('lags', lags_grid)
  }
  return search_space


results_search, frozen_trial = bayesian_search_forecaster(
  forecaster         = forecaster,
  y                  = data.loc[:end_valid, 'temp'], # Test data not used
  search_space       = search_space,
  steps              = 36,
  refit              = False,
  metric             = 'mean_absolute_percentage_error',
  initial_train_size = len(data.loc[:end_train]),
  fixed_train_size   = False,
  n_trials           = 20, # Increase this value for a more exhaustive search
  random_state       = 123,
  return_best        = True,
  n_jobs             = 'auto',
  verbose            = False,
  show_progress      = True
)

best_params = results_search['params'].iat[0]

  0%|          | 0/20 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/optuna/distributions.py:524: UserWarning: Choices for a categorical distribution should be a tuple of None, bool, int, float and str for persistent storage but contains [1, 2, 3, 4, 7, 9, 24] which is of type list.
  warnings.warn(message)


`Forecaster` refitted using the best-found lags and parameters, and the whole data set: 
  Lags: [ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24] 
  Parameters: {'max_iter': 1000, 'max_depth': 5, 'learning_rate': 0.2345829390285611, 'min_samples_leaf': 12, 'l2_regularization': 0.7194689697855631}
  Backtesting metric: 0.03885126036488121



/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(


In [17]:
forecaster = ForecasterAutoreg(
  regressor = HistGradientBoostingRegressor(**best_params,
                  random_state=123),
  lags = 24
  )

In [19]:
forecaster.fit(y=data.loc[:end_valid, 'temp'])

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_discretization.py:322: UserWarning: Bins whose width are too small (i.e., <= 1e-8) in feature 0 are removed. Consider decreasing the number of bins.
  warnings.warn(


In [20]:
# make predictions into the future
predictions = forecaster.predict(
  steps    = 26
)
df_preds = pd.DataFrame(predictions)

In [21]:
df_preds

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


pred
2022-01-01  10.078714
2022-02-01   8.926764
2022-03-01   8.681183
2022-04-01   9.228129
2022-05-01  10.555031
2022-06-01  12.214826
2022-07-01  13.437551
2022-08-01  14.305771
2022-09-01  14.242987
2022-10-01  13.417754
2022-11-01  12.076354
2022-12-01  10.078714
2023-01-01   9.510893
2023-02-01   8.775791
2023-03-01   8.959969
2023-04-01   9.604639
2023-05-01  10.653091
2023-06-01  11.788259
2023-07-01  12.020133
2023-08-01  13.427512
2023-09-01  13.829913
2023-10-01  13.792926
2023-11-01  13.500256
2023-12-01  12.502920
2024-01-01  10.849860
2024-02-01   9.755809